# Attack on Firmware Implementation of AES (Acquisition + Visualization + DPA + CPA) based on CW code :-)

First you'll need to select which hardware setup you have. You'll need to select a `SCOPETYPE`, a `PLATFORM`, and a `CRYPTO_TARGET`. `SCOPETYPE` can either be `'OPENADC'` for the CWLite/CW1200 or `'CWNANO'` for the CWNano. `PLATFORM` is the target device, with `'CWLITEARM'`/`'CW308_STM32F3'` being the best supported option, followed by `'CWLITEXMEGA'`/`'CW308_XMEGA'`, then by `'CWNANO'`. `CRYPTO_TARGET` selects the crypto implementation, with `'TINYAES128C'` working on all platforms. An alternative for `'CWLITEXMEGA'` targets is `'AVRCRYPTOLIB'`. For example:

```python
SCOPETYPE = 'OPENADC'
PLATFORM = 'CWLITEARM'
CRYPTO_TARGET='TINYAES128C'
SS_VER='SS_VER_1_1'
```

In [ ]:
SCOPETYPE = 'OPENADC'
PLATFORM = 'CWLITEARM'
CRYPTO_TARGET='TINYAES128C'
SS_VER='SS_VER_1_1'

The following code will build the firmware for the target.

In [ ]:
%run "../../Setup_Scripts/Setup_Generic.ipynb"

In [ ]:
%%bash -s "$PLATFORM" "$CRYPTO_TARGET" "$SS_VER"
cd ../../../hardware/victims/firmware/simpleserial-aes
make PLATFORM=$1 CRYPTO_TARGET=$2 SS_VER=$3

In [ ]:
cw.program_target(scope, prog, "../../../hardware/victims/firmware/simpleserial-aes/simpleserial-aes-{}.hex".format(PLATFORM))

We should need less than 100 traces this time to break AES, but for NANO let's take 200 :-D !

In [ ]:
from tqdm.notebook import trange
import numpy as np
import time

ktp = cw.ktp.Basic()
trace_array = []
textin_array = []

key, text = ktp.next()

target.set_key(key)

N = 100 #increase nano reliability
if PLATFORM=="CWNANO":
    N = 200
for i in trange(N, desc='Capturing traces'):
    scope.arm()
    
    target.simpleserial_write('p', text)
    
    ret = scope.capture()
    if ret:
        print("Target timed out!")
        continue
    
    response = target.simpleserial_read('r', 16)
    
    trace_array.append(scope.get_last_trace())
    textin_array.append(text)
    
    key, text = ktp.next()
    
trace_array = np.array(trace_array)

We don't need the hardware anymore, so we'll disconnect:

In [ ]:
scope.dis()
target.dis()

### Plot the first and last trace using matplotlib. Use for example:
%matplotlib notebook

import matplotlib.pylab as plt

Also please print the key. 

## Different settings for acquistion

### Please experiment with different settings for acquision. 

Check:
https://chipwhisperer.readthedocs.io/en/latest/scope-api.html#api-scope-cwnano

Try modyfying: scope.adc.samples 

Read and print other settings of scope.adc 

## Alignment

### The traces seems very aligned. Why do you think it is the case? 

How would you implement countermeasures here?Which code is actually run?

Let's concentrate on random delays. 

### Recombile the code for random delays and check the traces. 





## How to write and read traces and data?